In [3]:
# pip install tritonclient[http] ipykernel ipywidgets numpy scipy
!mkdir -p ../wavs
import numpy as np
SAMPLING_RATE = 22050
from tritonclient.utils import *
from IPython.display import Audio
from scipy.io.wavfile import write
import tritonclient.http as httpclient
triton_client = httpclient.InferenceServerClient(url="localhost:8011")

In [11]:
source_data = np.array([['this']], dtype='object')
inputs = [httpclient.InferInput("INPUT_TEXT", source_data.shape, np_to_triton_dtype(source_data.dtype)), httpclient.InferInput("INPUT_SPEAKER_ID", source_data.shape, np_to_triton_dtype(source_data.dtype)), httpclient.InferInput("INPUT_LANGUAGE_ID", source_data.shape, np_to_triton_dtype(source_data.dtype))]
inputs[0].set_data_from_numpy(np.array([['this is a spartfa!']], dtype='object'))
inputs[1].set_data_from_numpy(np.array([['m']], dtype='object'))
inputs[2].set_data_from_numpy(np.array([['hi']], dtype='object'))
outputs = [httpclient.InferRequestedOutput("OUTPUT_GENERATED_AUDIO")]
result = triton_client.infer(model_name='tts', inputs=inputs, outputs=outputs)
result = np.frombuffer(result.as_numpy('OUTPUT_GENERATED_AUDIO')[0][0], dtype='int16')
write('../wavs/test.wav', SAMPLING_RATE, result)
display(Audio(f"../wavs/test.wav"))